In [ ]:
# Required packages (run this in a cell)
!pip install pedalboard
!pip install ipywidgets
!pip install matplotlib
!pip install scipy
!pip install numpy
!pip install IPython

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.0/58.0 kB 1.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.8/4.8 MB 11.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 8.7 MB/s eta 0:00:00


In [ ]:
# -*- coding: utf-8 -*-
"""
Parallel Modulated Gated Reverb with Frequency Shifting
Jupyter Notebook Implementation

Features:
- Real-time audio processing using Pedalboard
- Parallel modulated reverb processing
- Frequency shifting effects
- Gated reverb envelope control
- Interactive parameter adjustment
"""

import numpy as np
import matplotlib.pyplot as plt
from scipy.io import wavfile
from scipy import signal
import pedalboard
from pedalboard import Reverb, Gain, Phaser, PitchShift
from IPython.display import Audio, display
import ipywidgets as widgets
from io import BytesIO
import base64

In [ ]:
class ParallelModulatedReverb:
    """
    Parallel modulated gated reverb with frequency shifting
    """
    def __init__(self, sample_rate=44100):
        self.sample_rate = sample_rate
        self.setup_effects()

    def setup_effects(self):
        """Initialize all audio effects"""
        # Main reverb with modulation
        self.reverb = Reverb(
            room_size=0.7,
            damping=0.5,
            wet_level=0.3,
            dry_level=0.7,
            width=0.8,
            freeze_mode=0
        )

        # Frequency shifter
        self.pitch_shift = PitchShift(semitones=0)

        # Modulation effects
        self.phaser = Phaser(
            rate_hz=0.5,
            depth=0.7,
            centre_frequency_hz=800,
            feedback=0.4,
            mix=0.3
        )

        self.gain = Gain(gain_db=0)

    def create_gate_envelope(self, audio, attack_ms=5, release_ms=100):
        """Create gated reverb envelope"""
        attack_samples = int(attack_ms * self.sample_rate / 1000)
        release_samples = int(release_ms * self.sample_rate / 1000)

        # Create envelope
        envelope = np.ones_like(audio)
        if len(audio.shape) > 1:
            envelope = envelope[:, 0]  # Use first channel

        # Apply attack and release
        if attack_samples > 0:
            attack_env = np.linspace(0, 1, attack_samples)
            envelope[:attack_samples] = attack_env

        if release_samples > 0:
            release_env = np.linspace(1, 0, release_samples)
            envelope[-release_samples:] = release_env

        return envelope

    def process_audio(self, audio, params):
        """
        Process audio with parallel modulated reverb and frequency shifting

        Parameters:
        audio: input audio signal
        params: dictionary of effect parameters
        """
        # Update effect parameters
        self.reverb.room_size = params['room_size']
        self.reverb.wet_level = params['reverb_wet']
        self.reverb.dry_level = params['reverb_dry']
        self.pitch_shift.semitones = params['pitch_shift']
        self.phaser.rate_hz = params['phaser_rate']
        self.phaser.depth = params['phaser_depth']
        self.gain.gain_db = params['gain_db']

        # Process dry signal
        dry_signal = audio * params['dry_mix']

        # Process reverb path
        reverb_signal = self.reverb(audio, self.sample_rate)

        # Apply frequency shifting
        if params['pitch_shift'] != 0:
            reverb_signal = self.pitch_shift(reverb_signal, self.sample_rate)

        # Apply phaser modulation
        reverb_signal = self.phaser(reverb_signal, self.sample_rate)

        # Apply gated envelope
        if params['gate_enabled']:
            gate_env = self.create_gate_envelope(
                reverb_signal,
                params['gate_attack'],
                params['gate_release']
            )
            if len(reverb_signal.shape) > 1:
                reverb_signal = reverb_signal * gate_env[:, np.newaxis]
            else:
                reverb_signal = reverb_signal * gate_env

        # Apply gain
        reverb_signal = self.gain(reverb_signal, self.sample_rate)

        # Mix dry and wet signals
        wet_mix = reverb_signal * params['wet_mix']
        output = dry_signal + wet_mix

        # Normalize to prevent clipping
        max_val = np.max(np.abs(output))
        if max_val > 1.0:
            output = output / max_val

        return output

In [ ]:
def create_ui_controls():
    """Create interactive UI controls"""
    style = {'description_width': '150px'}
    layout = widgets.Layout(width='300px')

    controls = {
        'room_size': widgets.FloatSlider(
            value=0.7, min=0.1, max=1.0, step=0.1,
            description='Room Size:', style=style, layout=layout
        ),
        'reverb_wet': widgets.FloatSlider(
            value=0.3, min=0.0, max=1.0, step=0.1,
            description='Reverb Wet:', style=style, layout=layout
        ),
        'reverb_dry': widgets.FloatSlider(
            value=0.7, min=0.0, max=1.0, step=0.1,
            description='Reverb Dry:', style=style, layout=layout
        ),
        'pitch_shift': widgets.FloatSlider(
            value=0.0, min=-12.0, max=12.0, step=0.5,
            description='Pitch Shift:', style=style, layout=layout
        ),
        'phaser_rate': widgets.FloatSlider(
            value=0.5, min=0.1, max=5.0, step=0.1,
            description='Phaser Rate:', style=style, layout=layout
        ),
        'phaser_depth': widgets.FloatSlider(
            value=0.7, min=0.0, max=1.0, step=0.1,
            description='Phaser Depth:', style=style, layout=layout
        ),
        'gain_db': widgets.FloatSlider(
            value=0.0, min=-24.0, max=24.0, step=1.0,
            description='Output Gain:', style=style, layout=layout
        ),
        'dry_mix': widgets.FloatSlider(
            value=0.7, min=0.0, max=1.0, step=0.1,
            description='Dry Mix:', style=style, layout=layout
        ),
        'wet_mix': widgets.FloatSlider(
            value=0.3, min=0.0, max=1.0, step=0.1,
            description='Wet Mix:', style=style, layout=layout
        ),
        'gate_enabled': widgets.Checkbox(
            value=True, description='Enable Gate', style=style
        ),
        'gate_attack': widgets.FloatSlider(
            value=5.0, min=1.0, max=100.0, step=1.0,
            description='Gate Attack (ms):', style=style, layout=layout
        ),
        'gate_release': widgets.FloatSlider(
            value=100.0, min=10.0, max=500.0, step=10.0,
            description='Gate Release (ms):', style=style, layout=layout
        )
    }

    return controls

# Create UI controls
ui_controls = create_ui_controls()

In [ ]:
def upload_audio(change):
    """Handle audio file upload"""
    global audio_data, sample_rate, original_audio

    try:
        # Read uploaded audio
        uploaded = change['owner']
        audio_bytes = uploaded.value

        # Read WAV file
        sample_rate, audio_data = wavfile.read(BytesIO(audio_bytes))

        # Convert to float32 and stereo if needed
        if audio_data.dtype != np.float32:
            audio_data = audio_data.astype(np.float32) / np.iinfo(audio_data.dtype).max

        if len(audio_data.shape) == 1:
            audio_data = np.column_stack([audio_data, audio_data])

        original_audio = audio_data.copy()

        print(f"Audio loaded: {sample_rate}Hz, {audio_data.shape}")

    except Exception as e:
        print(f"Error loading audio: {e}")

def process_and_play(b):
    """Process audio with current settings and play result"""
    try:
        # Get current parameter values
        params = {name: control.value for name, control in ui_controls.items()}

        # Initialize processor
        processor = ParallelModulatedReverb(sample_rate)

        # Process audio
        processed_audio = processor.process_audio(original_audio, params)

        # Play processed audio
        display(Audio(processed_audio.T, rate=sample_rate, autoplay=True))

        # Plot results
        plot_results(original_audio, processed_audio, sample_rate)

    except Exception as e:
        print(f"Error processing audio: {e}")

def plot_results(original, processed, sr):
    """Plot original and processed audio waveforms"""
    plt.figure(figsize=(12, 8))

    # Time axis
    time = np.arange(len(original)) / sr

    # Plot original
    plt.subplot(2, 1, 1)
    plt.plot(time, original[:, 0], alpha=0.7)
    plt.title('Original Audio')
    plt.xlabel('Time (s)')
    plt.ylabel('Amplitude')
    plt.grid(True, alpha=0.3)

    # Plot processed
    plt.subplot(2, 1, 2)
    plt.plot(time, processed[:, 0], alpha=0.7, color='orange')
    plt.title('Processed Audio')
    plt.xlabel('Time (s)')
    plt.ylabel('Amplitude')
    plt.grid(True, alpha=0.3)

    plt.tight_layout()
    plt.show()

In [ ]:
# File upload widget
upload = widgets.FileUpload(
    description='Upload Audio',
    accept='.wav,.mp3',
    multiple=False
)
upload.observe(upload_audio, names='value')

# Process button
process_btn = widgets.Button(
    description='Process & Play',
    button_style='success',
    tooltip='Process audio with current settings'
)
process_btn.on_click(process_and_play)

# Create UI layout
ui_layout = widgets.VBox([
    widgets.HTML("<h2>Audio Upload</h2>"),
    upload,
    widgets.HTML("<h2>Effect Parameters</h2>"),
    *ui_controls.values(),
    process_btn
])

display(ui_layout)

In [ ]:
# Example of real-time processing with shorter audio
def create_test_signal():
    """Create a test signal for demonstration"""
    sr = 44100
    duration = 3.0
    t = np.linspace(0, duration, int(sr * duration))

    # Create a simple test signal
    test_signal = 0.5 * np.sin(2 * np.pi * 440 * t)
    test_signal += 0.3 * np.sin(2 * np.pi * 880 * t)

    return test_signal, sr

# Generate test signal
test_audio, test_sr = create_test_signal()
test_audio = np.column_stack([test_audio, test_audio])

# Process with default settings
processor = ParallelModulatedReverb(test_sr)
params = {name: control.value for name, control in ui_controls.items()}
processed_test = processor.process_audio(test_audio, params)

# Play test result
print("Test signal with default settings:")
display(Audio(processed_test.T, rate=test_sr, autoplay=False))

Test signal with default settings:
